In [1]:
import os; os.chdir('..')

In [2]:
import pandas as pd

In [3]:
original_df= pd.read_csv("data/data_for_seo_new_intent.csv")
original_df.head()

keyword         intent
0       social media groups  informational
1       social media groups   navigational
2           internet forums   navigational
3       virtual communities   navigational
4  online discussion boards     commercial

In [3]:
def map_intent(intent:str):
    return intent.lower()

In [4]:
temp_df= pd.read_csv("data_intent/intent_data.csv")
temp_df.intent= temp_df.intent.map(map_intent)
temp_df= temp_df[temp_df.intent!="local"]
temp_df.head()

keyword         intent
0               citalopram vs prozac     commercial
1  who is the oldest football player  informational
2                 t mobile town east   navigational
3                          starbucks   navigational
4                        tech crunch   navigational

In [5]:
# original_df= temp_df.copy()

In [6]:
original_df= pd.concat([original_df, temp_df])

In [6]:
original_df.duplicated().value_counts()

False    1304
True      196
Name: count, dtype: int64

In [7]:
# original_df.drop_duplicates(inplace=True)

In [8]:
original_df.duplicated().value_counts()

False    1304
True      196
Name: count, dtype: int64

In [9]:
original_df= original_df[original_df.intent!='Local']

In [10]:
intents= original_df.intent.unique().tolist()
intents

['commercial', 'informational', 'navigational', 'transactional']

In [11]:
id2label= {}
label2id= {}
for i in range(len(intents)):
    id2label[i]= intents[i]
    label2id[intents[i]]= i

In [12]:
id2label

{0: 'commercial', 1: 'informational', 2: 'navigational', 3: 'transactional'}

In [13]:
label2id

{'commercial': 0, 'informational': 1, 'navigational': 2, 'transactional': 3}

In [14]:
def make_label2id(label):
    return label2id[label]

In [15]:
original_df['id']= original_df.intent.map(make_label2id)
original_df

keyword         intent  id
0                                  citalopram vs prozac     commercial   0
1                     who is the oldest football player  informational   1
2                                    t mobile town east   navigational   2
3                                             starbucks   navigational   2
4                                           tech crunch   navigational   2
...                                                 ...            ...  ..
1703  How to make homemade pet accessories from recy...  informational   1
1704  Top 10 science fiction book series that take r...  informational   1
1705  How to start a car restoration and customizati...  informational   1
1706  Ancient Mesopotamian architecture and its infl...  informational   1
1707  Benefits of a flexitarian diet for those seeki...  informational   1

[1500 rows x 3 columns]

In [16]:
# df= original_df[['metatitle', 'id']]
df= original_df[['keyword', 'id']]
df

keyword  id
0                                  citalopram vs prozac   0
1                     who is the oldest football player   1
2                                    t mobile town east   2
3                                             starbucks   2
4                                           tech crunch   2
...                                                 ...  ..
1703  How to make homemade pet accessories from recy...   1
1704  Top 10 science fiction book series that take r...   1
1705  How to start a car restoration and customizati...   1
1706  Ancient Mesopotamian architecture and its infl...   1
1707  Benefits of a flexitarian diet for those seeki...   1

[1500 rows x 2 columns]

In [17]:
df= df.sample(frac=1).reset_index(drop=True)

df

keyword  id
0                           Buy baby stroller   3
1     Why do leaves change color in the fall?   1
2       How to improve your leadership skills   1
3                             sneakers amazon   3
4              Shop for photography equipment   3
...                                       ...  ..
1495                    Why do stars twinkle?   1
1496         Buy eco-friendly beauty products   0
1497                         Order makeup kit   3
1498                                   Lowe's   2
1499                Get photography equipment   3

[1500 rows x 2 columns]

In [18]:
from datasets import Dataset, load_dataset


/home/ubuntu/FineTunedDistilledBertAIChecker/venv/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [19]:
df.rename(columns={
    "keyword": "text", 
    # "metatitle": "text", 
    "id": "label"
}, 
          inplace=True
)

df.sample(10)

text  label
870   Important space missions to the New Horizons s...      1
947            How to start a travel and adventure blog      1
477        How to improve your critical thinking skills      1
174                      How to make homemade baby food      1
1369                  Cheap sustainable clothing brands      0
396           Exploring the mysteries of the deep ocean      1
206                 Discounted eco-friendly patio decor      0
191                  Cheap eco-friendly office products      0
533                             Affordable pet supplies      0
1398                              Travel tips for Japan      1

In [20]:
dataset_df= Dataset.from_pandas(df)
dataset_df

Dataset({
    features: ['text', 'label'],
    num_rows: 1500
})

In [21]:
new_data= dataset_df.train_test_split(test_size=0.25)
new_data

DatasetDict({
    train: Dataset({
        features: ['text', 'label'],
        num_rows: 1125
    })
    test: Dataset({
        features: ['text', 'label'],
        num_rows: 375
    })
})

In [22]:
from transformers import AutoTokenizer

tokenizer = AutoTokenizer.from_pretrained("distilbert-base-uncased")

In [23]:
def preprocess_function(examples):
    return tokenizer(examples["text"], truncation=True)

In [24]:
tokenized_df = new_data.map(preprocess_function, batched=True)


Map: 100%|██████████| 375/375 [00:00<00:00, 29503.00 examples/s]


In [25]:
# from transformers import DataCollatorWithPadding

# data_collator = DataCollatorWithPadding(tokenizer=tokenizer, return_tensors="tf")




from transformers import DataCollatorWithPadding

data_collator = DataCollatorWithPadding(tokenizer=tokenizer)

2023-11-04 12:46:03.199613: I tensorflow/core/util/port.cc:111] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2023-11-04 12:46:03.249373: E tensorflow/compiler/xla/stream_executor/cuda/cuda_dnn.cc:9342] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2023-11-04 12:46:03.249409: E tensorflow/compiler/xla/stream_executor/cuda/cuda_fft.cc:609] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2023-11-04 12:46:03.249439: E tensorflow/compiler/xla/stream_executor/cuda/cuda_blas.cc:1518] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2023-11-04 12:46:03.257947: I tensorflow/core/platform/cpu_feature_g

In [26]:
import evaluate

accuracy = evaluate.load("accuracy")

In [27]:
import numpy as np


def compute_metrics(eval_pred):
    predictions, labels = eval_pred
    predictions = np.argmax(predictions, axis=1)
    return accuracy.compute(predictions=predictions, references=labels)

In [28]:
from transformers import AutoModelForSequenceClassification, TrainingArguments, Trainer

model = AutoModelForSequenceClassification.from_pretrained(
    # "distilbert-base-uncased", num_labels=5, id2label=id2label, label2id=label2id
    # "distilbert-base-uncased", num_labels=4, id2label=id2label, label2id=label2id # removed local
    "bert-base-uncased", num_labels=4, id2label=id2label, label2id=label2id # removed local
)

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [29]:
training_args = TrainingArguments(
    output_dir="intent_classification_model_without_metatitle_with_local23",
    learning_rate=2e-5,
    per_device_train_batch_size=16,
    per_device_eval_batch_size=16,
    num_train_epochs=6,
    weight_decay=0.01,
    evaluation_strategy="epoch",
    save_strategy="epoch",
    load_best_model_at_end=True,
    # push_to_hub=True,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_df["train"],
    eval_dataset=tokenized_df["test"],
    tokenizer=tokenizer,
    data_collator=data_collator,
    compute_metrics=compute_metrics,
)

trainer.train()

You're using a DistilBertTokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


TrainOutput(global_step=426, training_loss=0.1806535676051753, metrics={'train_runtime': 57.2339, 'train_samples_per_second': 117.937, 'train_steps_per_second': 7.443, 'total_flos': 44042600979624.0, 'train_loss': 0.1806535676051753, 'epoch': 6.0})